Work done so far: change all data types, drop some corrupted rows with at start_time and end_time
Delete all rows with null value.
Calculating idle time (station-level)

Import weather data

Next: working on weather and location data.
Visualize each part
Decide on which regression models we should use


In [1]:
# import all relevant libraries
import pandas as pd

import numpy as np
import matplotlib.pyplot as plt
from pandas.plotting import register_matplotlib_converters

register_matplotlib_converters()
import seaborn as sns

sns.set()
sns.set_style("white")
sns.set_palette("GnBu_d")

# also import these "new" libraries
# Note: you may have to download an add them to your environment (using e.g. 'conda install -c conda-forge folium')
import folium
from folium import plugins
from folium.plugins import HeatMap
from datetime import datetime  # for working with times objects
from datetime import timedelta  # for working with times objects
import math
import random

c:\Users\riven\anaconda3\lib\site-packages\scipy\__init__.py:146: UserWarning: A NumPy version >=1.16.5 and <1.23.0 is required for this version of SciPy (detected version 1.24.3
  warnings.warn(f"A NumPy version >={np_minversion} and <{np_maxversion}"


## Step 1: Import Data 

In [2]:
# load csv file and set the index column by 0
df = pd.read_csv("baywheels_2019", encoding="ISO-8859-1", index_col=0)
df.head(20)

c:\Users\riven\anaconda3\lib\site-packages\IPython\core\interactiveshell.py:3444: DtypeWarning: Columns (3,4,5,6,7,8,9) have mixed types.Specify dtype option on import or set low_memory=False.
  exec(code_obj, self.user_global_ns, self.user_ns)


start_time             end_time start_station_id  \
0   2019-10-28 09:46:47  2019-10-28 09:51:05             50.0   
1   2019-08-10 19:31:02  2019-08-10 19:35:05            285.0   
2   2019-05-27 13:18:58  2019-05-27 13:46:37             10.0   
3   2019-07-24 22:47:58  2019-07-24 22:52:48            106.0   
4   2019-04-28 17:26:22  2019-04-28 17:31:54             80.0   
5   2019-04-17 19:39:05  2019-04-17 19:49:26            100.0   
6   2019-02-26 08:11:01  2019-02-26 08:22:58             67.0   
7   2019-02-02 09:23:15  2019-02-02 09:34:20             44.0   
8   2019-05-07 12:08:01  2019-05-07 12:12:00              9.0   
9   2019-09-04 21:58:19  2019-09-04 22:09:07             86.0   
10  2019-06-12 18:04:25  2019-06-12 18:15:57            241.0   
11  2019-08-31 13:12:58  2019-08-31 13:34:22            304.0   
12  2019-10-17 08:56:41  2019-10-17 09:02:35             61.0   
13  2019-02-12 07:11:41  2019-02-12 07:15:22            223.0   
14  2019-03-13 11:36:57  2019-03-13 11:45:29            252.0   
15  2019-02-01 11:38:20  2019-02-01 11:53:14            139.0   
16  2019-07-10 17:16:46  2019-07-10 17:23:22             79.0   
17  2019-07-28 13:49:45  2019-07-28 14:17:33              NaN   
18  2019-12-23 09:06:10  2019-12-23 09:10:45            323.0   
19  2019-01-10 09:55:28  2019-01-10 09:59:27            223.0   

   start_station_lat start_station_lon end_station_id end_station_lat  \
0          37.780526       -122.390288          453.0       37.777934   
1          37.783521       -122.431158           74.0       37.776435   
2          37.795393        -122.40477          399.0       37.802636   
3          37.763242       -122.430675           72.0       37.772406   
4          37.775235       -122.397437           50.0       37.780526   
5            37.7671       -122.410662           74.0       37.776435   
6          37.776639       -122.395526            8.0       37.799953   
7          37.781074       -122.411738           55.0       37.777053   
8          37.798572       -122.400869            6.0        37.80477   
9          37.769305       -122.426826           39.0       37.778999   
10         37.852477       -122.270213          271.0       37.855783   
11         37.348759       -121.894798          282.0       37.332426   
12         37.776513       -122.411306           90.0       37.771058   
13         37.764765       -122.420091          100.0         37.7671   
14         37.865847       -122.267443          241.0       37.852477   
15         37.751017       -122.411901          104.0       37.767045   
16         37.773492       -122.403672           44.0       37.781074   
17         37.806791       -122.419491            NaN       37.798469   
18         37.798014        -122.40595           14.0       37.795001   
19         37.764765       -122.420091          112.0       37.763847   

   end_station_lon   bike_id  
0      -122.396973   12424.0  
1      -122.426244    1718.0  
2      -122.436289     608.0  
3       -122.43565  551642.0  
4      -122.390288    1103.0  
5      -122.426244    1473.0  
6      -122.398525    4984.0  
7      -122.429558    2666.0  
8      -122.403234    1961.0  
9      -122.436861    9717.0  
10     -122.283127     840.0  
11     -121.890349    3412.0  
12     -122.402717   12353.0  
13     -122.410662    5185.0  
14     -122.270213    5172.0  
15     -122.390833    4813.0  
16     -122.411738    1312.0  
17     -122.401155  928582.0  
18      -122.39997   12895.0  
19     -122.413004     845.0

In [3]:
# take a look at the data types and general information
print(df.info())
print(df.describe())

<class 'pandas.core.frame.DataFrame'>
Int64Index: 2507003 entries, 0 to 2507002
Data columns (total 9 columns):
 #   Column             Dtype 
---  ------             ----- 
 0   start_time         object
 1   end_time           object
 2   start_station_id   object
 3   start_station_lat  object
 4   start_station_lon  object
 5   end_station_id     object
 6   end_station_lat    object
 7   end_station_lon    object
 8   bike_id            object
dtypes: object(9)
memory usage: 191.3+ MB
None
       start_time end_time  start_station_id  start_station_lat  \
count     2507003  2507003         2426269.0       2.507003e+06   
unique    2304544  2303004             867.0       7.712800e+04   
top       Failure  Failure              58.0       3.777662e+01   
freq           10       10           34467.0       3.446700e+04   

        start_station_lon  end_station_id  end_station_lat  end_station_lon  \
count        2.507003e+06       2424101.0     2.507003e+06     2.507003e+06   
unique

We can see that the data types are not specified which makes it hard to work with. After inspecting the dataset, there are rows containing "Failure" so we want to remove all of these. 

In [4]:
# create a new data frame that containts all failure rows from dft
rent_failure = df["start_time"].str.contains("Failure")
data_failure = df[rent_failure]
data_failure

start_time end_time start_station_id start_station_lat  \
381556     Failure  Failure          Failure           Failure   
485428     Failure  Failure          Failure           Failure   
621119     Failure  Failure          Failure           Failure   
713198     Failure  Failure          Failure           Failure   
1150787    Failure  Failure          Failure           Failure   
1558857    Failure  Failure          Failure           Failure   
1676023    Failure  Failure          Failure           Failure   
1697405    Failure  Failure          Failure           Failure   
1999499    Failure  Failure          Failure           Failure   
2249494    Failure  Failure          Failure           Failure   

        start_station_lon end_station_id end_station_lat end_station_lon  \
381556            Failure        Failure         Failure         Failure   
485428            Failure        Failure         Failure         Failure   
621119            Failure        Failure         Failure         Failure   
713198            Failure        Failure         Failure         Failure   
1150787           Failure        Failure         Failure         Failure   
1558857           Failure        Failure         Failure         Failure   
1676023           Failure        Failure         Failure         Failure   
1697405           Failure        Failure         Failure         Failure   
1999499           Failure        Failure         Failure         Failure   
2249494           Failure        Failure         Failure         Failure   

         bike_id  
381556   Failure  
485428   Failure  
621119   Failure  
713198   Failure  
1150787  Failure  
1558857  Failure  
1676023  Failure  
1697405  Failure  
1999499  Failure  
2249494  Failure

In [5]:
# remove all rows that match failure rows
df = df.drop(data_failure.index, axis=0)

## Step 2: Transform Data

Now we have to convert every feature to the correct data types in order to to make calculations and analysis.

In [6]:
df["bike_id"]= pd.to_numeric(df["bike_id"], errors='coerce')
df["bike_id"]= df["bike_id"].astype('Int64')
df["start_station_lat"]= pd.to_numeric(df["start_station_lat"], errors='coerce')
df["start_station_lon"]=pd.to_numeric(df["start_station_lon"], errors='coerce')
df["end_station_lat"]=pd.to_numeric(df["end_station_lat"], errors='coerce')
df["end_station_lon"]=pd.to_numeric(df["end_station_lon"], errors='coerce')
df["start_station_id"] =pd.to_numeric(df["start_station_id"], errors='coerce')
df["start_station_id"]= df["start_station_id"].astype("Int64")
df["end_station_id"] =pd.to_numeric(df["end_station_id"], errors='coerce')
df["end_station_id"]= df["end_station_id"].astype("Int64")
df['start_station_lat'] = df['start_station_lat'].round(5)
df['start_station_lon'] = df['start_station_lon'].round(5)
df['end_station_lat'] = df['end_station_lat'].round(5)
df['end_station_lon'] = df['end_station_lon'].round(5)

df["start_time"]= pd.to_datetime(df["start_time"],format ='%Y-%m-%d %H:%M:%S')
df["end_time"]= pd.to_datetime(df["end_time"],format ='%Y-%m-%d %H:%M:%S')
print(df.info())

<class 'pandas.core.frame.DataFrame'>
Int64Index: 2506993 entries, 0 to 2507002
Data columns (total 9 columns):
 #   Column             Dtype         
---  ------             -----         
 0   start_time         datetime64[ns]
 1   end_time           datetime64[ns]
 2   start_station_id   Int64         
 3   start_station_lat  float64       
 4   start_station_lon  float64       
 5   end_station_id     Int64         
 6   end_station_lat    float64       
 7   end_station_lon    float64       
 8   bike_id            Int64         
dtypes: Int64(3), datetime64[ns](2), float64(4)
memory usage: 198.4 MB
None


In [7]:
# After transforming the data we check if there are any non-defined values.
df.isna().sum()

start_time               0
end_time                 0
start_station_id     80734
start_station_lat        0
start_station_lon        0
end_station_id       82902
end_station_lat          0
end_station_lon          0
bike_id                  1
dtype: int64

## Step 3: Handle missing and incorrect values

Firstly, we noticed that there are entries which have invalid start or end time (not in 2019). Since the amount of it is less than 5%, we can remove these.

In [8]:
# drop some rows with start_time in 2013
df.drop(df[(df['start_time'].dt.year < 2018) | (df['start_time'].dt.year > 2020)].index, inplace=True)

Secondly, there are missing values in <b>start_station_id</b> and <b>end_station_id</b> column. We tried different approaches to handle these values:
- Using <b>k-means clustering algorithm</b> to assign an ID to the given longtitudes and latitudes.

- <b>Dropping</b> all rows with missing values.

The cost of performing the first method was higher than the latter and the amount of missing values take up less than 5%, so we decided to opt for the second approach.

In [9]:
df.drop(df[df['start_station_id'].isnull() | df['end_station_id'].isnull()].index, inplace = True)
#drop rows where start_time start after end_time
df.drop(df[df["start_time"] > df["end_time"]].index, inplace = True)

In [38]:
df_dup = df[['start_station_id', 'start_station_lat', 'start_station_lon']].copy()
start_station_dup = df_dup.groupby(['start_station_id','start_station_lat', 'start_station_lon']).size()
start_station_dup = start_station_dup.to_frame(name = 'size').reset_index()
start_station_dup.drop_duplicates(inplace=True)
start_station_dup.drop_duplicates(subset = "start_station_id", inplace = True)


In [39]:
end_station_dup = df[['end_station_id', 'end_station_lat', 'end_station_lon']].copy()
end_station_dup = end_station_dup.groupby(['end_station_id','end_station_lat', 'end_station_lon']).size()
end_station_dup = end_station_dup.to_frame(name = 'size').reset_index()
end_station_dup.drop_duplicates(inplace=True)
end_station_dup.drop_duplicates(subset = "end_station_id", inplace = True)


In [40]:
df_new = pd.merge(df, start_station_dup, on = 'start_station_id', how = 'left')


In [41]:
df_new = pd.merge(df_new, end_station_dup, on = 'end_station_id', how = 'left')
df_new


start_time            end_time  start_station_id  \
0       2019-10-28 09:46:47 2019-10-28 09:51:05                50   
1       2019-08-10 19:31:02 2019-08-10 19:35:05               285   
2       2019-05-27 13:18:58 2019-05-27 13:46:37                10   
3       2019-07-24 22:47:58 2019-07-24 22:52:48               106   
4       2019-04-28 17:26:22 2019-04-28 17:31:54                80   
...                     ...                 ...               ...   
2407243 2019-04-12 19:11:48 2019-04-12 19:17:34               109   
2407244 2019-07-16 19:02:32 2019-07-16 19:06:54                58   
2407245 2019-05-29 16:03:26 2019-05-29 16:09:25                23   
2407246 2019-08-19 08:32:17 2019-08-19 08:41:26                23   
2407247 2019-04-02 17:00:36 2019-04-02 17:06:28                64   

         start_station_lat_x  start_station_lon_x  end_station_id  \
0                   37.78053           -122.39029             453   
1                   37.78352           -122.43116              74   
2                   37.79539           -122.40477             399   
3                   37.76324           -122.43067              72   
4                   37.77523           -122.39744              50   
...                      ...                  ...             ...   
2407243             37.76332           -122.42190             381   
2407244             37.77662           -122.41738               5   
2407245             37.79146           -122.39103              15   
2407246             37.79146           -122.39103             364   
2407247             37.77675           -122.39902               3   

         end_station_lat_x  end_station_lon_x  bike_id  start_station_lat_y  \
0                 37.77793         -122.39697    12424             37.78053   
1                 37.77643         -122.42624     1718             37.78352   
2                 37.80264         -122.43629      608             37.79539   
3                 37.77241         -122.43565   551642             37.76324   
4                 37.78053         -122.39029     1103             37.77523   
...                    ...                ...      ...                  ...   
2407243           37.75824         -122.42609     6118             37.76332   
2407244           37.78390         -122.40844     1479             37.77662   
2407245           37.79539         -122.39420     1742             37.79146   
2407246           37.77200         -122.38997    10107             37.79146   
2407247           37.78638         -122.40490     5359             37.77675   

         start_station_lon_y  size_x  end_station_lat_y  end_station_lon_y  \
0                 -122.39029   24280           37.77793         -122.39697   
1                 -122.43116    8938           37.77643         -122.42624   
2                 -122.40477    9465           37.80264         -122.43629   
3                 -122.43067    4184           37.77241         -122.43565   
4                 -122.39744   15475           37.78053         -122.39029   
...                      ...     ...                ...                ...   
2407243           -122.42190   12598           37.75824         -122.42609   
2407244           -122.41738   44769           37.78390         -122.40844   
2407245           -122.39103   19128           37.79539         -122.39420   
2407246           -122.39103   19128           37.77200         -122.38997   
2407247           -122.39902    9958           37.78638         -122.40490   

         size_y  
0          2190  
1         12247  
2          6569  
3          5319  
4         25535  
...         ...  
2407243    2073  
2407244   31407  
2407245   47925  
2407246   10183  
2407247   37259  

[2407248 rows x 15 columns]

In [42]:
df_new.drop(['start_station_lat_x',	'start_station_lon_x','end_station_lat_x','end_station_lon_x','size_x','size_y'],axis= 1,inplace=True)

df_new

start_time            end_time  start_station_id  \
0       2019-10-28 09:46:47 2019-10-28 09:51:05                50   
1       2019-08-10 19:31:02 2019-08-10 19:35:05               285   
2       2019-05-27 13:18:58 2019-05-27 13:46:37                10   
3       2019-07-24 22:47:58 2019-07-24 22:52:48               106   
4       2019-04-28 17:26:22 2019-04-28 17:31:54                80   
...                     ...                 ...               ...   
2407243 2019-04-12 19:11:48 2019-04-12 19:17:34               109   
2407244 2019-07-16 19:02:32 2019-07-16 19:06:54                58   
2407245 2019-05-29 16:03:26 2019-05-29 16:09:25                23   
2407246 2019-08-19 08:32:17 2019-08-19 08:41:26                23   
2407247 2019-04-02 17:00:36 2019-04-02 17:06:28                64   

         end_station_id  bike_id  start_station_lat_y  start_station_lon_y  \
0                   453    12424             37.78053           -122.39029   
1                    74     1718             37.78352           -122.43116   
2                   399      608             37.79539           -122.40477   
3                    72   551642             37.76324           -122.43067   
4                    50     1103             37.77523           -122.39744   
...                 ...      ...                  ...                  ...   
2407243             381     6118             37.76332           -122.42190   
2407244               5     1479             37.77662           -122.41738   
2407245              15     1742             37.79146           -122.39103   
2407246             364    10107             37.79146           -122.39103   
2407247               3     5359             37.77675           -122.39902   

         end_station_lat_y  end_station_lon_y  
0                 37.77793         -122.39697  
1                 37.77643         -122.42624  
2                 37.80264         -122.43629  
3                 37.77241         -122.43565  
4                 37.78053         -122.39029  
...                    ...                ...  
2407243           37.75824         -122.42609  
2407244           37.78390         -122.40844  
2407245           37.79539         -122.39420  
2407246           37.77200         -122.38997  
2407247           37.78638         -122.40490  

[2407248 rows x 9 columns]

In [46]:
df_new.rename(columns={'start_station_lat_y':'start_station_lat','start_station_lon_y':'start_station_lon','end_station_lat_y': 'end_station_lat','end_station_lon_y':'end_station_lon'},inplace=True)


In [49]:
new_column_order = ['start_time','end_time','start_station_id','start_station_lat',	'start_station_lon','end_station_id','end_station_lat','end_station_lon','bike_id']
df_new= df_new[new_column_order]

In [23]:
coords = start_station_dup[['start_station_lat', 'start_station_lon']]
coords.start_station_lat.dtype
lat = coords.start_station_lat.tolist()
lon = coords.start_station_lon.tolist()
point_list = list(zip(lat,lon))
map = folium.Map(point_list[0], zoom_start =12, control_scale = True)

for p in point_list:
    folium.Marker(location = p, popup = str(p[0]) + str(p[1])).add_to(map)

map

float

In [ ]:
df.hist(bins = 12, figsize = (20, 10))

Something can be interpreted from the above graph:
the stations with the station_id under 150 are more occupied than the rest, maybe they are located within city center?




Now let's try to calculate idle time
2 approach: idle time group by bike_id, and idle time group by station_id



Let's go with the second approach


In [ ]:
start_stations =df.loc[:,['start_time', 'start_station_id', 'bike_id']]
start_stations["rented"] = 1
start_stations.rename(columns = {"start_time": "timestamp", 'start_station_id': "station_id"}, inplace=True)
start_stations


Now we want to try the second approach.

In [ ]:
end_stations =df.loc[:,['end_time', 'end_station_id', 'bike_id']]
end_stations["rented"] = 0
end_stations.rename(columns={"end_time": "timestamp", 'end_station_id': "station_id"}, inplace=True)
end_stations

In [ ]:
df_merged = pd.concat([start_stations, end_stations], axis = 0)
df_merged = df_merged.sort_values(by = ["station_id", "timestamp"])
df_merged['idle_time'] = pd.Timedelta(0)
df_merged

We define a function that calculates idle time with the help of a nested loop inside the dataframe

In [ ]:


def idle_cal(df):
    
    df = df.groupby('station_id')
    results = []  # List to store the modified groups
    for group_name, group_data in df:
        group_data.sort_values(by = 'timestamp', inplace = True)
        group_data.reset_index(drop=True, inplace=True)
    
        group_data['prev_row'] = group_data.groupby("station_id")['timestamp'].shift(1)
        for i, row in group_data.iterrows():
            if i != 0:
                if row['rented'] == 1:
                    idle_time = pd.Timedelta(0)
                    #print('idle at i ', i , ':', idle_time)
                    j = i - 1 
                    while j>=1 and group_data.at[j,'rented'] == 0:
                        idle_time = group_data.at[i,'timestamp'] -  group_data.at[j,'timestamp']
                        group_data.at[j,'idle_time'] = idle_time
                        #print('idle at j ', j , ':',  idle_time)
                        j -= 1
                    
        results.append(group_data)

    modified_df = (pd.concat(results, ignore_index=True))
    df = pd.DataFrame(modified_df)
    return df
    
                    
        

              


In [ ]:
df_merged = idle_cal(df_merged)
df_merged.head(100)

In [ ]:
df_merged.to_csv('idle_time_calculated')  

In [ ]:
notnull =df_merged[df_merged['idle_time']!=pd.Timedelta(0)]
print(notnull)

In [6]:
df_w_idle_time = pd.read_csv("idle_time_calculated")
idle_time_per_trip = df_w_idle_time[df_w_idle_time['rented'] == 0]


In [ ]:
df_w_idle_time.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 4814518 entries, 0 to 4814517
Data columns (total 6 columns):
 #   Column      Dtype 
---  ------      ----- 
 0   Unnamed: 0  int64 
 1   timestamp   object
 2   station_id  int64 
 3   bike_id     int64 
 4   rented      int64 
 5   idle_time   object
dtypes: int64(4), object(2)
memory usage: 220.4+ MB


In [7]:
df_w_idle_time['timestamp']= pd.to_datetime(df_w_idle_time['timestamp'],format ='%Y-%m-%d %H:%M:%S')

In [8]:

df_w_idle_time['sum_idle_time']= pd.Timedelta(0)
df_w_idle_time['idle_mode_count']= 0
df_w_idle_time['month']= df_w_idle_time['timestamp'].dt.month

#df_w_idle_time.head(10)


In [9]:
def get_weekday(ts):
    return ts.weekday()


In [10]:
df_w_idle_time['day']= df_w_idle_time['timestamp'].dt.day
df_w_idle_time['hour']= df_w_idle_time['timestamp'].dt.hour
df_w_idle_time['day_of_week']= df_w_idle_time["timestamp"].apply(lambda x: get_weekday(x))


In [11]:
df_w_idle_time

Unnamed: 0           timestamp  station_id  bike_id  rented  \
0                 0 2019-01-01 01:05:01           3     5426       0   
1                 1 2019-01-01 01:11:19           3     5481       1   
2                 2 2019-01-01 01:23:27           3     5216       1   
3                 3 2019-01-01 01:40:07           3     5426       1   
4                 4 2019-01-01 05:03:40           3     5191       1   
...             ...                 ...         ...      ...     ...   
4814513     4814513 2019-12-30 14:29:13         498    10962       0   
4814514     4814514 2019-12-30 14:29:36         498    10962       1   
4814515     4814515 2019-12-30 14:36:08         498    10962       0   
4814516     4814516 2019-12-31 11:29:00         498    10962       1   
4814517     4814517 2019-12-31 12:17:46         498    10962       0   

               idle_time sum_idle_time  idle_mode_count  month  day  hour  \
0        0 days 00:06:18        0 days                0      1    1     1   
1        0 days 00:00:00        0 days                0      1    1     1   
2        0 days 00:00:00        0 days                0      1    1     1   
3        0 days 00:00:00        0 days                0      1    1     1   
4        0 days 00:00:00        0 days                0      1    1     5   
...                  ...           ...              ...    ...  ...   ...   
4814513  0 days 00:00:23        0 days                0     12   30    14   
4814514  0 days 00:00:00        0 days                0     12   30    14   
4814515  0 days 20:52:52        0 days                0     12   30    14   
4814516  0 days 00:00:00        0 days                0     12   31    11   
4814517  0 days 00:00:00        0 days                0     12   31    12   

         day_of_week  
0                  1  
1                  1  
2                  1  
3                  1  
4                  1  
...              ...  
4814513            0  
4814514            0  
4814515            0  
4814516            1  
4814517            1  

[4814518 rows x 12 columns]

In [19]:
def sum_idle_cal(df):
    
    df = df.groupby('station_id')
    results = {}  # dict to store the modified groups
    
    for group_name, group_data in df:
        group_data.sort_values(by = 'timestamp', inplace = True)
        group_data.reset_index(drop=True, inplace=True)
        sum_idle_time= pd.Timedelta(0)
        idle_mode_count = 0
    
        for i, row in group_data.iterrows():
            if i != 0:
                j = i - 1
                
                if row['rented']==0 and group_data.at[j,'rented'] == 1:
                    sum_idle_time += group_data.at[j,'sum_idle_time']+ group_data.at[i,'idle_time']
                    idle_mode_count +=1
                else:
                    sum_idle_time += group_data.at[j,'sum_idle_time']
                    
            else:
                sum_idle_time+= group_data.at[i,'idle_time']
                
                idle_mode_count+= 1
    
        
        results[str(group_name)] = [sum_idle_time, idle_mode_count]
            
                    
                    
                    
            
    

    return results

In [28]:
def monthly_idle_sum(month):
    df = df_w_idle_time[df_w_idle_time['month'] == month]
    idle_in_month = sum_idle_cal(df)
    df = pd.DataFrame(columns= ["station_id", "idle_sum", "idle_count"])
    df["station_id"] = idle_in_month.keys()
    modified_values = list(zip(*idle_in_month.values()))
    df["idle_sum"] = modified_values[0]
    df["idle_count"] = modified_values[1]
    df["idle_avg"] = (df["idle_sum"]/ df["idle_count"]).dt.round('1s')
    df['month']= month
    return df

In [29]:
#Do not run this
jan= monthly_idle_sum(1)
feb= monthly_idle_sum(2)
mar= monthly_idle_sum(3)
apr= monthly_idle_sum(4)
may= monthly_idle_sum(5)
jun= monthly_idle_sum(6)
jul= monthly_idle_sum(7)
aug= monthly_idle_sum(8)
sep= monthly_idle_sum(9)
oct= monthly_idle_sum(10)
nov= monthly_idle_sum(11)
dec= monthly_idle_sum(12)



In [32]:
# Do not run this
monthly_df_summary= pd.concat([jan,feb,mar,apr,may,jun,jul,aug,sep,oct,nov,dec], axis = 0)
monthly_df_summary['station_id']=pd.to_numeric(monthly_df_summary['station_id'])
monthly_df_summary= monthly_df_summary.sort_values(['month','station_id'])
monthly_df_summary


station_id         idle_sum  idle_count        idle_avg  month
0             3 13 days 01:04:12        1472 0 days 00:12:46      1
1             4 10 days 20:36:26         321 0 days 00:48:43      1
2             5 12 days 04:06:56        1212 0 days 00:14:28      1
3             6 18 days 03:41:10        1095 0 days 00:23:52      1
4             7 11 days 22:48:27         305 0 days 00:56:25      1
..          ...              ...         ...             ...    ...
417         492  7 days 18:55:37          22 0 days 08:29:48     12
418         493 17 days 18:13:17         161 0 days 02:38:50     12
419         494  6 days 03:54:03           6 1 days 00:39:00     12
420         495 12 days 23:35:16          13 0 days 23:58:06     12
421         498  4 days 12:13:47           7 0 days 15:27:41     12

[4493 rows x 5 columns]

In [33]:
monthly_df_summary.to_csv("monthly sum and average per station")

In [12]:
df_w_idle_time_copy = df_w_idle_time.copy()
df_w_idle_time_copy['idle_time'] = pd.to_timedelta(df_w_idle_time['idle_time']).dt.total_seconds()/60
print(df_w_idle_time_copy['idle_time'])

0             6.300000
1             0.000000
2             0.000000
3             0.000000
4             0.000000
              ...     
4814513       0.383333
4814514       0.000000
4814515    1252.866667
4814516       0.000000
4814517       0.000000
Name: idle_time, Length: 4814518, dtype: float64


In [19]:
#dont run
max_idle_time = df_w_idle_time_copy['idle_time'].max()
print(max_idle_time)

max_station = df_w_idle_time_copy[round(df_w_idle_time_copy['idle_time']) == round(max_idle_time)]
print(max_station)

112155.01666666666
         Unnamed: 0           timestamp  station_id  bike_id  rented   
4305678     4305678 2019-03-18 13:07:36         344     6215       0  \

             idle_time sum_idle_time  idle_mode_count  month  day  hour   
4305678  112155.016667        0 days                0      3   18    13  \

         day_of_week  
4305678            0  


In [13]:
hour = df_w_idle_time_copy[df_w_idle_time_copy["rented"] == 0]["hour"]
idle_time = df_w_idle_time_copy[df_w_idle_time_copy["rented"] == 0]["idle_time"]
idle_time = [round(x) for x in idle_time]
print(idle_time)

[6, 113, 108, 98, 31, 26, 25, 17, 17, 3, 1, 32, 12, 12, 12, 12, 9, 10, 2, 1, 1, 6, 6, 44, 19, 19, 1, 14, 6, 1, 19, 16, 14, 7, 1, 18, 12, 6, 5, 9, 39, 39, 39, 28, 21, 14, 4, 15, 10, 15, 12, 6, 54, 35, 18, 17, 166, 3, 25, 11, 28, 24, 17, 5, 5, 9, 8, 0, 0, 1, 1, 0, 0, 1, 6, 2, 13, 11, 8, 8, 7, 0, 27, 27, 20, 14, 13, 11, 6, 1, 1, 7, 6, 3, 1, 6, 4, 3, 27, 19, 0, 32, 22, 13, 11, 5, 21, 15, 7, 1, 1, 1, 16, 7, 21, 16, 7, 6, 15, 9, 4, 3, 2, 2, 8, 4, 4, 31, 31, 29, 28, 16, 16, 5, 28, 28, 25, 5, 2, 3, 8, 4, 1, 1, 3, 0, 1, 5, 5, 4, 1, 9, 10, 6, 1, 2, 2, 7, 1, 0, 8, 8, 11, 6, 0, 5, 59, 11, 64, 34, 6, 22, 17, 16, 36, 24, 14, 13, 11, 7, 5, 2, 1, 5, 4, 2, 7, 0, 11, 7, 3, 3, 2, 0, 7, 5, 2, 2, 1, 1, 1, 0, 8, 7, 1, 18, 9, 3, 12, 8, 2, 1, 5, 3, 0, 72, 39, 37, 18, 15, 38, 38, 32, 8, 3, 15, 14, 1, 29, 3, 1, 0, 6, 5, 0, 12, 1, 3, 3, 1, 0, 0, 3, 1, 1, 0, 6, 6, 6, 6, 1, 1, 1, 5, 0, 6, 4, 2, 3, 3, 1, 1, 1, 0, 3, 1, 2, 2, 2, 0, 8, 3, 5, 1, 13, 12, 0, 13, 2, 18, 6, 4, 3, 36, 24, 370, 118, 84, 15, 5, 11, 9, 12, 8,

In [14]:
avg_values = df_w_idle_time_copy[(df_w_idle_time_copy["rented"] == 0) & (df_w_idle_time_copy["idle_time"] > 0.0)].groupby('hour')['idle_time'].mean()
print(avg_values)

hour
0     358.193809
1     330.618529
2     333.821144
3     265.824640
4     193.959576
5     116.505993
6      67.477305
7      42.193631
8      36.835221
9      44.474508
10     62.722174
11     69.985569
12     69.045411
13     76.809550
14     73.433805
15     72.527267
16     62.244171
17     63.918300
18     90.953594
19    132.605991
20    183.558893
21    240.336702
22    295.538146
23    335.532310
Name: idle_time, dtype: float64


In [48]:
plt.xlabel("Hour")
plt.ylabel("Average Idle time")
x_values = range(0,24,1) 
plt.plot(x_values,avg_values, color = "red") 
plt.ylim(0,500)
plt.xticks(range(0, 24, 1))
plt.figure(figsize = (20,10))
plt.show()

<Figure size 2000x1000 with 0 Axes>

In [15]:
fig,ax = plt.subplots(figsize=(10,4)) 
sns.boxplot(x=hour, y= idle_time)
#plt.ylim(0,600)


<Axes: xlabel='hour'>

## Step 3b: Working with Weather Data

First approaches:

In [ ]:
# import the weather data
wd = pd.read_csv("SanFrancisco", encoding="ISO-8859-1", index_col=0)
# show first 20 rows
wd.head(20)

In [ ]:
# take a look at the data types and general information
print(wd.info())
print(wd.describe())

In [ ]:
# convert timestamp to datetime
wd['timestamp'] = pd.to_datetime(wd['timestamp'],format ='%Y-%m-%d %H:%M:%S')

# extract the year from timestamp
wd['year'] = wd['timestamp'].dt.year

# count how many entries are for what year
value_counts = wd['year'].value_counts()

# show how many entries has every year, because only 2019 is important
print(value_counts)


In [ ]:
print(wd.info())

In [ ]:
# only the data for the year 2019 is important, so we drop all the other entries.
wd = wd[wd['timestamp'].dt.year == 2019]


In [ ]:
# check first 20 entries to look is it was successfull
wd.head(20)

In [ ]:
# after transforming the data we check if there are any non-defined values.
wd.isna().sum()

In [ ]:
# drop all rows with missing values
weather_2019 = wd.dropna(axis = 0)
print(weather_2019.info())
print(weather_2019.describe())

In [ ]:
# let's have a look at the temperature in Sanfrancisco in 2019
fig,ax = plt.subplots(figsize=(10,4))
ax.plot(weather_2019["timestamp"],weather_2019["temperature"])
ax.set_xlabel("Date")
ax.set_ylabel("Grad")
ax.set_title("Temperature in Sanfrancisco in 2019")
plt.show()


Our goal is to find out how would the weather affect the bike rent business. With the help of idle_time could we analyze under what kinf of weather (e.g Temperature, Windspeed) where should we put our bikes, so that they can be rented as frequently as possible. We assume that normally when the temparature is high, people would go out like beach, and when it's cold, people would spend time in city center like shopping mall. Then we can separate the weather data in seasons to have a better look.

In [ ]:
# create month feature
weather_2019["Month"] = weather_2019["timestamp"].apply(lambda dt: dt.month)
weather_2019.head()

In [ ]:
# create four seasons
spring_month=[3,4,5]
spring_2019 = weather_2019[weather_2019["Month"].isin(spring_month)==True]

summer_month=[6,7,8]
summer_2019 = weather_2019[weather_2019["Month"].isin(summer_month)==True]

autumn_month=[9,10,11]
autumn_2019 = weather_2019[weather_2019["Month"].isin(autumn_month)==True]

winter_month=[12,1,2]
winter_2019 = weather_2019[weather_2019["Month"].isin(winter_month)==True]

summer_2019.head(10)